### CT -> 24 slices png

In [16]:

import nibabel as nib
import numpy as np
from pathlib import Path
import matplotlib.pyplot as plt

INPUT_DIR = Path("/home/tibia/Documents/pacs-ai/pacs-ai-backend/model-examples/BrainGPT/temp/") #CHEMIN CT NII GZ Ici
SLICE_OUTPUT_DIR = INPUT_DIR / "slices_png"
SLICE_OUTPUT_DIR.mkdir(parents=True, exist_ok=True)

nii_files = list(INPUT_DIR.glob("*.nii.gz"))

for file in nii_files:
    img = nib.load(str(file))
    data = img.get_fdata()  # shape (H, W, D) où D > 24
    base_name = file.stem  # sans extension

    # Le nombre de tranches total dans le volume
    total_slices = data.shape[2]
    
    # Vérification: s'il y a moins de 24 tranches, on ne peut pas en sélectionner 24.
    if total_slices < 24:
        print(f"  {file.name} ignoré (seulement {total_slices} tranches)")
        continue


    selected_indices = np.linspace(0, total_slices - 1, 24).astype(int)

    # Sauvegarde les slices sélectionnées
    for i, slice_index in enumerate(selected_indices):
        slice_2d = data[:, :, slice_index]
        
        # Normalisation simple [0, 255]
        slice_norm = 255 * (slice_2d - np.min(slice_2d)) / (np.ptp(slice_2d) + 1e-8)
        slice_uint8 = slice_norm.astype(np.uint8)


        out_path = SLICE_OUTPUT_DIR / f"{base_name}_slice_sample_{i:02d}.png"
        plt.imsave(out_path, slice_uint8, cmap="gray")

    print(f"  {file.name} : 24 tranches (équidistantes) sauvegardées dans {SLICE_OUTPUT_DIR}")
    
    


### Renaming correcte pour que braingpt fonctionne

In [17]:
png_files = sorted(SLICE_OUTPUT_DIR.glob("*.png"))

for f in png_files:
    old_name = f.name  # ex: ID_441cea72_ID_4b13324a92.nii_slice00.png vient du RSNA

    parts = old_name.split("_")
    if len(parts) < 2:
        continue

    # On garde seulement les chiffres pour la première partie après ID pour que loadimage marche
    first_id = ''.join(filter(str.isdigit, parts[1]))  # '441cea72' -> '44172'

    # On fait meme pour la deuxieme partie
    second_id = ''.join(filter(str.isdigit, parts[3].split(".")[0]))  # '4b13324a92' -> '4132492'

    # Slice et extension
    slice_and_ext = "_".join(parts[4:])  # ex: slice00.png

    # Nouveau nom
    new_name = f"ID_{first_id}_ID_{second_id}_{slice_and_ext}"
    new_path = f.parent / new_name

    print(f"Renaming: {old_name} -> {new_name}")
    f.rename(new_path)

Renaming: ID_00526c11_ID_d6296de728.nii_slice_sample_00.png -> ID_0052611_ID_6296728_slice_sample_00.png
Renaming: ID_00526c11_ID_d6296de728.nii_slice_sample_01.png -> ID_0052611_ID_6296728_slice_sample_01.png
Renaming: ID_00526c11_ID_d6296de728.nii_slice_sample_02.png -> ID_0052611_ID_6296728_slice_sample_02.png
Renaming: ID_00526c11_ID_d6296de728.nii_slice_sample_03.png -> ID_0052611_ID_6296728_slice_sample_03.png
Renaming: ID_00526c11_ID_d6296de728.nii_slice_sample_04.png -> ID_0052611_ID_6296728_slice_sample_04.png
Renaming: ID_00526c11_ID_d6296de728.nii_slice_sample_05.png -> ID_0052611_ID_6296728_slice_sample_05.png
Renaming: ID_00526c11_ID_d6296de728.nii_slice_sample_06.png -> ID_0052611_ID_6296728_slice_sample_06.png
Renaming: ID_00526c11_ID_d6296de728.nii_slice_sample_07.png -> ID_0052611_ID_6296728_slice_sample_07.png
Renaming: ID_00526c11_ID_d6296de728.nii_slice_sample_08.png -> ID_0052611_ID_6296728_slice_sample_08.png
Renaming: ID_00526c11_ID_d6296de728.nii_slice_sample_09

### Création du .json encondant les images en base 64

In [24]:
import subprocess

# Chemins
script_dir = "/home/tibia/Documents/pacs-ai/pacs-ai-backend/model-examples/BrainGPT/MIIT/mimic-it/convert-it" # CHEMIN DU SCRIPT main.py de MIIT
image_path = SLICE_OUTPUT_DIR


command = [
    "python", 
    "main.py", 
    "--name=change.SpotTheDifference", 
    f"--image_path={image_path}", 
    "--num_threads=4"
]

print("Lancement du script...")

# Exécution
try:
    result = subprocess.run(
        command, 
        cwd=script_dir,  
        check=True,      
        capture_output=True, 
        text=True       
    )
    print("Succès !")
    print(result.stdout) 
    
except subprocess.CalledProcessError as e:
    print("Erreur lors de l'exécution :")
    print(e.stderr) # Affiche l'erreur
    

Lancement du script...
Succès !
Fichiers trouvés : 24
 type du dataset <class 'dict'>
 contenu: {'ID_0052611_ID_6296728_slice_sample_10': b'\x89PNG\r\n\x1a\n\x00\x00\x00\rIHDR\x00\x00\x02\x00\x00\x00\x02\x00\x08\x06\x00\x00\x00\xf4x\xd4\xfa\x00\x00\x00:tEXtSoftware\x00Matplotlib version3.10.7, https://matplotlib.org/L\xb1#T\x00\x00\x00\tpHYs\x00\x00\x0fa\x00\x00\x0fa\x01\xa8?\xa7i\x00\x01\x00\x00IDATx\x9c\xec\xbd\xe9v#9\xb24\x08\xa66j\xcb\xa5\xaa\xab\xbf\x99\xf7\x7f\xb8\x99{\xbb\xab2S+\xb5r~\xd4X\xa4\xd1\xe4\x0e8\x96 \xa9\xac\xf4st$\x91\x08l\x01\xb8\x9b\x1b\x1c\xc0"\xa5\xb4NAY,\x16\x1b\xbf\xf9\xf3\xf5:\x9c\x8d\xf9\xac\xfe\xde\xa6\xec\xa2\xccV\xd1\xbe\x87D\xea\xef=[#ZNM\x9eV\x1d\xad\xe79\x9d~\x9f\xfb\xaeU\xa2\xf9\xf0\xf8_,\x16\xe9\xc3\x87\x0f\xe9\xc3\x87\x0f\xe9\xe8\xe8(\x9d\x9c\x9c\xa4\xd3\xd3\xd3tvv\x96NOO\xd3\xc9\xc9I:>>N\xc7\xc7\xc7\xe9\xe0\xe0 \x1d\x1d\x1d\xa5\x83\x83\x83t||\x9c\x0e\x0f\x0f\xd3\xe1\xe1a\xfa\xf0\xe1C:88\x98\xf2\xe3\xbcG\xb6/\'\xb9q3w\xf9\x1f>|x\xf3\xd9\xeb\xeb\xab\x

### Création du .json d'instruction pour mapping avec prompt et images

In [ ]:
# Code pour faire le .json d'instruction 

import os
import json
import glob
from collections import defaultdict


# Chemin vers le dossier contenant les images brutes
dataset_path = "/home/tibia/Documents/pacs-ai/pacs-ai-backend/model-examples/BrainGPT/temp/slices_png"

# Nom court du dataset (doit être le même que dans main.py)
short_name = "PACS_AI"

# L'instruction à donner au modèle
INSTRUCTION_TEXT = (
    "You are an AI assistant specialized in radiology topics. "
    " Which organs do these CT slices belong to? "
    
    # "You are provided with brain CT slices from a single study. "
    # "The number of slices is {num_slices}. "
    # "Please generate medical descriptions based on the images in a consistent style. "
    # "Use the following guidelines: - Degree: Indicate the intensity or state (e.g., normal, mild, chronic, old, etc). "
    # "- Landmark: Specify the area of interest (e.g., intracerebral, midline, parenchyma, sulci, etc). "
    # "- Feature: Describe any observed abnormalities (e.g., hemorrhage, atrophy, infarcts, etc). "
    # "- Impression: Conclude with a clinical impression (e.g., arteriosclerotic encephalopathy, intracerebral hemorrhage, dementia, etc). "
    # "Ensure consistency and clarity in the report."
)

# =================================================

def generate_instruction_json(dataset_path=dataset_path):
    # 1. Lister les images
    extensions = ["*.png", "*.jpg", "*.jpeg", "*.bmp"]
    all_files = []
    for ext in extensions:
        all_files.extend(glob.glob(os.path.join(dataset_path, ext)))
    
    if not all_files:
        all_files = [os.path.join(dataset_path, f) for f in os.listdir(dataset_path) 
                     if f.lower().endswith(('.png', '.jpg', '.jpeg', '.bmp'))]

    # 2. Grouper les images par "Étude" (Patient ID)
    studies = defaultdict(list)

    print(f"Traitement de {len(all_files)} fichiers...")

    for file_path in all_files:
        filename = os.path.basename(file_path)
        
        # --- Etape A : Générer l'ID unique de l'image (pour le lien vers le Registry) ---
        name_without_ext = os.path.splitext(filename)[0]
        clean_name = name_without_ext.replace(".nii", "").replace(".", "_")
        full_image_id = f"{short_name}_IMG_{clean_name}"
        
        # --- Etape B : Identifier l'étude (Patient) ---
        # Ex: ID_1423bd41_ID_72db71a879.nii_slice_sample_01.png
        # On coupe avant "_slice_sample_" pour avoir le nom du patient
        if "_slice_sample_" in filename:
            study_id_raw = filename.split("_slice_sample_")[0]
            
            # Récupération du numéro de slice pour le tri
            try:
                slice_num_str = filename.split("_slice_sample_")[-1].split(".")[0]
                slice_num = int(slice_num_str)
            except:
                slice_num = 0
            
            studies[study_id_raw].append((slice_num, full_image_id))
        else:
            print(f"Ignoré (format incorrect) : {filename}")

    # 3. Construire le JSON final
    json_output = {
        "meta": {
            "version": "0.0.2",
            "time": "2024-02",
            "author": "big_data_center"
        },
        "data": {}
    }

    print(f"Génération des instructions pour {len(studies)} études...")

    for study_id_raw, slices in studies.items():
        # IMPORTANT : Trier les slices dans l'ordre (0, 1, 2...)
        slices.sort(key=lambda x: x[0])
        sorted_image_ids = [item[1] for item in slices]
        
        # MODIFICATION ICI : Création de la clé basée sur le nom réel
        # On nettoie un peu le nom (enlève .nii et remplace les points par _)
        # Ex: ID_1423bd41.nii -> ID_1423bd41
        clean_study_key = study_id_raw.replace(".nii", "").replace(".", "_")
        
        # On peut ajouter un préfixe pour faire propre, ou laisser tel quel.
        # Ici je mets "INS_" + le nom réel pour indiquer que c'est une instruction.
        ins_key = f"INS_{clean_study_key}" 
        
        # Mise à jour du texte avec le vrai nombre de slices
        current_instruction = INSTRUCTION_TEXT.format(num_slices=len(sorted_image_ids))

        json_output["data"][ins_key] = {
            "instruction": current_instruction,
            "answer": "",
            "image_ids": sorted_image_ids,
            "rel_ins_ids": []
        }

    # 4. Sauvegarde
    output_filename = "instruction_dataset.json"
    with open(output_filename, "w") as f:
        json.dump(json_output, f, indent=4)

    print(f"Terminé ! Fichier '{output_filename}' généré.")
    
generate_instruction_json()

Traitement de 24 fichiers...
Génération des instructions pour 1 études...
Terminé ! Fichier 'instruction_dataset.json' généré.


### Chargement du modèle  

In [11]:
import sys
import os


otter_path = "/home/tibia/Documents/pacs-ai/pacs-ai-backend/model-examples/BrainGPT"

if otter_path not in sys.path:
    sys.path.append(otter_path)
    print(f"Ajout de {otter_path} au sys.path")
    
    
flamingo_path_parent = "/home/tibia/Documents/pacs-ai/pacs-ai-backend/model-examples/BrainGPT/otter"
if flamingo_path_parent not in sys.path:
    sys.path.append(flamingo_path_parent)
    print(f"Ajout de {flamingo_path_parent} au sys.path (pour 'flamingo')")

Ajout de /home/tibia/Documents/pacs-ai/pacs-ai-backend/model-examples/BrainGPT/otter au sys.path (pour 'flamingo')


In [12]:
import torch

from otter.modeling_otter import OtterForConditionalGeneration

model = OtterForConditionalGeneration.from_pretrained(
                "/home/tibia/Documents/LLM/BrainGPT/checkpoints/OTTER_CLIP_BRAINGPT_hf/" 
                ) # ICI REMPLACER PAR VRAI CHEMIN /home/tibia/Documents/pacs-ai/pacs-ai-backend/model-examples/BrainGPT/models

# Affichez le modèle pour vérifier qu'il est chargé 
print(f"Modèle chargé : {type(model)}")

tokenizer = model.text_tokenizer

/home/tibia/Documents/LLM/BrainGPT/braingpt_env/lib/python3.10/site-packages/huggingface_hub/file_download.py:945: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(


You are using config.init_device='cpu', but you can also use config.init_device="meta" with Composer + FSDP for fast initialization.


/home/tibia/Documents/pacs-ai/pacs-ai-backend/model-examples/BrainGPT/otter/flamingo/mpt/param_init_fns.py:28: UserWarning: Using a non-tuple sequence for multidimensional indexing is deprecated and will be changed in pytorch 2.9; use x[tuple(seq)] instead of x[seq]. In pytorch 2.9 this will be interpreted as tensor index, x[torch.tensor(seq)], which will result either in an error or a different result (Triggered internally at /pytorch/torch/csrc/autograd/python_variable_indexing.cpp:306.)
  init_fn_(module.weight[slice_indices])
Using pad_token, but it is not set yet.


The current model version is configured for Otter-Image with max_num_frames set to None.
Total Trainable param: 1.385404 B


Loading checkpoint shards: 100%|██████████| 4/4 [00:18<00:00,  4.67s/it]
Some weights of OtterForConditionalGeneration were not initialized from the model checkpoint at /home/tibia/Documents/LLM/BrainGPT/checkpoints/OTTER_CLIP_BRAINGPT_hf/ and are newly initialized: ['vision_encoder.vision_model.embeddings.position_ids']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


Modèle chargé : <class 'otter.modeling_otter.OtterForConditionalGeneration'>


### Dataset adapté à Braingpt

In [27]:

# 1. Création d'une fausse classe d'arguments pour remplacer argparse braingpt
class SimpleArgs:
    def __init__(self, tokenizer):
        # Paramètres requis par MimicitDataset.__init__
        self.tokenizer = tokenizer
        self.task = "inference"
        self.max_src_length = 512      # Valeur par défaut standard
        self.max_tgt_length = 512      # Valeur par défaut standard
        self.seed = 42                 # Valeur par défaut standard
        self.patch_image_size = 224  # Taille standard des patchs image
        self.inst_format= "simple"
        
        # Paramètres pour le DataLoader
        self.workers = 1
        
        
import torch
from torch.utils.data import DataLoader
from mimicit_utils.mimicit_dataset import MimicitDataset

def get_inference_dataloader(args, tokenizer):
    
    
    """
    Version simplifiée pour l'inférence avec --mimicit_path et --images_path uniquement.
    """
    # 1. Configuration minimale requise par MimicitDataset
    args = SimpleArgs(tokenizer)
    
    # 2. Préparation des listes de chemins
    # MimicitDataset attend des listes, même pour un seul fichier
    mimicit_paths = ["/home/tibia/Documents/pacs-ai/pacs-ai-backend/model-examples/BrainGPT/temp/instruction_dataset.json"] # CHEMIN DU JSON D'INSTRUCTION
    image_paths = ["/home/tibia/Documents/pacs-ai/pacs-ai-backend/model-examples/BrainGPT/MIIT/mimic-it/convert-it/output/PACS_AI.json"] # CHEMIN DU JSON D'IMAGES PRODUIT PAR MIIT

    # Gestion de la config d'entraînement (vide mais necessaire poru compatibilité code)
    #  on passe une liste avec une chaîne vide
    train_config_paths = [""]
    
    # Statut des données (tout est "new" pour l'inférence)
    status_list = ["new"]

    print(f"Chargement du dataset depuis : {mimicit_paths[0]} et {image_paths[0]}")

    # 3. Création de l'instance du Dataset

    dataset = MimicitDataset(
        args, 
        mimicit_paths, 
        image_paths, 
        train_config_paths, 
        status_list=status_list
    )

    # 4. Création du DataLoader simple
    # - batch_size=1 : Pour traiter une image à la fois
    # - shuffle=False : IMPORTANT pour l'inférence (garder l'ordre des fichiers)
    # - drop_last=False : On veut traiter TOUTES les images, même si le compte n'est pas rond
    dataloader = DataLoader(
        dataset,
        batch_size=1, 
        num_workers=args.workers, # ou 1
        pin_memory=True,
        shuffle=False, 
        drop_last=False,
        collate_fn=dataset.collate # On garde la méthode de formatage du dataset
    )

    # On retourne directement le dataloader (pas une liste de dataloaders)
    return dataloader

In [28]:
device_id = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model.to(device_id)
batch_mimicit = next(iter(get_inference_dataloader(SimpleArgs(tokenizer), tokenizer)))

Chargement du dataset depuis : /home/tibia/Documents/pacs-ai/pacs-ai-backend/model-examples/BrainGPT/temp/instruction_dataset.json et /home/tibia/Documents/pacs-ai/pacs-ai-backend/model-examples/BrainGPT/MIIT/mimic-it/convert-it/output/PACS_AI.json
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


In [29]:

media_token_id = tokenizer("<image>", add_special_tokens=False)["input_ids"][-1]
endofchunk_token_id = tokenizer("<|endofchunk|>", add_special_tokens=False)["input_ids"][-1]
answer_token_id = tokenizer("<answer>", add_special_tokens=False)["input_ids"][-1]
ens_token_id = tokenizer(tokenizer.eos_token, add_special_tokens=False)["input_ids"][-1]

model.eval()


images = batch_mimicit["net_input"]["patch_images"].to(device_id, non_blocking=True)
input_ids = batch_mimicit["net_input"]["input_ids"].to(device_id, non_blocking=True)
attention_mask = batch_mimicit["net_input"]["attention_masks"].to(device_id, non_blocking=True)

labels = input_ids.clone()
labels[labels == tokenizer.pad_token_id] = -100
labels[:, 0] = -100
for i in range(labels.shape[0]):
                # remove loss for any token before the first <image> token
                # label_idx = 0
                # while label_idx < labels.shape[1] and labels[i][label_idx] != media_token_id:
                #     labels[i][label_idx] = -100
                #     label_idx += 1

                # <image>User: {cur_incontext_instruction} GPT:<answer> {cur_incontext_answer}<|endofchunk|>User: {instruction} GPT:<answer> {answer}<|endofchunk|>
                # <image>User: {cur_incontext_instruction} GPT:<answer> {cur_incontext_answer}<|endofchunk|><image>User: {instruction} GPT:<answer> {answer}<|endofchunk|>

                # get index of all endofchunk/media tokens in the sequence
    endofchunk_idxs = torch.where(labels[i] == endofchunk_token_id)[0]
    media_idxs = torch.where(labels[i] == media_token_id)[0]

                # remove loss for any token the before the first <answer>
    token_idx = 0
    while token_idx < labels.shape[1] and labels[i][token_idx] != answer_token_id:
        labels[i][token_idx] = -100
        token_idx += 1

                # remove loss for any token between <|endofchunk|> and <answer>, except <image>
        for endofchunk_idx in endofchunk_idxs[:-1]:
            token_idx = endofchunk_idx + 1
            while token_idx < labels.shape[1] and labels[i][token_idx] != answer_token_id:
                if labels[i][token_idx] == media_token_id:
                    pass
                else:
                    labels[i][token_idx] = -100
                    token_idx += 1

labels[labels == answer_token_id] = -100
labels[labels == media_token_id] = -100


### Prompt + Géneration du rapport

In [31]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model.to(device)
dtype = model.dtype

test_prompt = "Describe the image in a single sentence."
lang_x = model.text_tokenizer(
                    [f"<image>User: {test_prompt} GPT:<answer>"],
                    return_tensors="pt",
                )
print(f" lang x : {lang_x}")

lang_x_input_ids = lang_x["input_ids"].to(device)
lang_x_attention_mask = lang_x["attention_mask"].to(device)



generated_text = model.generate(
                    vision_x=images.to(dtype),
                    lang_x=lang_x_input_ids,
                    attention_mask=lang_x_attention_mask,
                    max_new_tokens = 512,
                ) 

# géneration du texte 
import pandas as pd

generated_captions = {}


parsed_output = (
                    model.text_tokenizer.decode(generated_text[0])
                    .split("<answer>")[-1]
                    .lstrip()
                    .rstrip()
                    .split("<|endofchunk|>")[0]
                    .lstrip()
                    .rstrip()
                    .lstrip('"')
                    .rstrip('"')
                )
gt = (
                    model.text_tokenizer.decode(input_ids[0])
                    .split("<answer>")[-1]
                    .lstrip()
                    .rstrip()
                    .split("<|endofchunk|>")[0]
                    .lstrip()
                    .rstrip()
                    .lstrip('"')
                    .rstrip('"')
                )
                # print(batch_mimicit.keys())
#                 print("/",parsed_output,"/")
generated_captions[batch_mimicit["id"][0]] = (gt, parsed_output)
                # print(generated_captions.keys())

    # print(generated_captions)
df_data = [(key, val[0], val[1]) for key, val in generated_captions.items()]
df = pd.DataFrame(df_data, columns=['id', 'gt', 'parsed_output'])
print(df)

df.to_csv("/home/tibia/Documents/pacs-ai/pacs-ai-backend/model-examples/BrainGPT/temp/output2", index=False)

Setting `pad_token_id` to `eos_token_id`:50277 for open-end generation.


 lang x : {'input_ids': tensor([[50278,  6989,    27,  3666, 19268,   253,  2460,   275,   247,  2014,
          6197,    15,   443,  5736,    27, 50279]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]])}
                          id gt  \
0  INS_ID_0052611_ID_6296728      

                                       parsed_output  
0  > Mild generalized atrophic change of the brai...  
